## Libraries and Methods

In [97]:
#Libraries
require 'net/http'
require 'json'
require 'csv'
require 'time'
require 'daru'

false

In [200]:
#Methods

def extract_pgn_params(input_string)
  parameters = input_string.split("\n").reject { |item| item.empty? }
  dict = {}
  
  parameters.each do |row|
    match = row.match(/\[([^"]+) "(.*?)"\]/)
  
    if match
      dict[match[1].to_sym] = match[2]
    else
      dict["pgn".to_sym] = row
    end
  end
    
  return dict 
end

def extract_time(params)
  date = params[:Date]
  time_utc = params[:UTCTime]
  
  t_time = Time.strptime("#{date}T#{time_utc}","%Y.%m.%dT%H:%M:%S")
  t_time_local = t_time.getlocal("+05:30")
end

def call_stats(opp_id, api_cache, t_type)
  if api_cache.key?(opp_id + "~" + t_type)
    return api_cache[opp_id + "~" + t_type]
  end
  
  url = "https://api.chess.com/pub/player/#{opp_id}/stats"
  puts url
  
  uri = URI.parse(url)
  
  rating = 
      case t_type
        when 'rapid', 'bullet', 'blitz', 'daily'
          response = Net::HTTP.get(uri)
          parsed_response = JSON.parse(response)
          parsed_response["chess_" + t_type]["last"]["rating"]
        else
          0
        end

  api_cache[opp_id + "~" + t_type] = rating

  return api_cache[opp_id + "~" + t_type]
end

def extract_moves(chess_string)
  chess_string.scan(/\d*\.+\s+([\w\d#]+)(?:\s*\{\[.*?\]\}\s*\})?\s*/).flatten.reject { |move| move =~ /\{|\}/ }
end

def opening_results(move_order, games, variation_move_no)
  opening_filter = games.filter(:row) do |row|
    row['moves_9'].start_with?(move_order) && row['moves_9'].split.size > 10
  end

  opening = opening_filter["moves_9","result"]
  opening_wins = opening['result'].filter{ |res| res == "WIN"}.size
  opening_draws = opening['result'].filter{ |res| res == "DRAW"}.size
  opening_losses = opening['result'].filter{ |res| res == "LOSE"}.size
  opening_net = opening_wins-opening_losses
  #print "Caro : ","+",opening_wins,"-",opening_losses,"=",opening_draws," net: [#{opening_net}]"

  opening['variation'] = opening['moves_9'].map { |moves| move_order + " [" + moves.split[variation_move_no] + "]" }
  return opening, opening_wins, opening_draws, opening_losses, opening_net
end

:opening_results

## Variables

In [167]:
# Chess.com username
username = '93codemonkey'        
# Time period (last month = -2; last 2 months = -3..-2)
months = -16..-5
# Output File
csv_file = 'archive_2023.csv'
# Read File
read_file = 'archive_2023.csv'

"archive_2023.csv"

## Chess.com API

In [168]:
url = URI.parse("https://api.chess.com/pub/player/#{username.downcase}/games/archives")

response = Net::HTTP.get(url)
month = JSON.parse(response)["archives"][months]

games_array = []

month = [month] if month.is_a?(String)
puts month

month.each do |mn|
  response = Net::HTTP.get(URI.parse(mn))
  games_array += JSON.parse(response)["games"]
end

puts "Reading #{games_array.size} games from #{month.slice(-7, 7)} archives [Chess.com]"

https://api.chess.com/pub/player/93codemonkey/games/2023/01
https://api.chess.com/pub/player/93codemonkey/games/2023/02
https://api.chess.com/pub/player/93codemonkey/games/2023/03
https://api.chess.com/pub/player/93codemonkey/games/2023/04
https://api.chess.com/pub/player/93codemonkey/games/2023/05
https://api.chess.com/pub/player/93codemonkey/games/2023/06
https://api.chess.com/pub/player/93codemonkey/games/2023/07
https://api.chess.com/pub/player/93codemonkey/games/2023/08
https://api.chess.com/pub/player/93codemonkey/games/2023/09
https://api.chess.com/pub/player/93codemonkey/games/2023/10
https://api.chess.com/pub/player/93codemonkey/games/2023/11
https://api.chess.com/pub/player/93codemonkey/games/2023/12
Reading 3443 games from ["https://api.chess.com/pub/player/93codemonkey/games/2023/06", "https://api.chess.com/pub/player/93codemonkey/games/2023/07", "https://api.chess.com/pub/player/93codemonkey/games/2023/08", "https://api.chess.com/pub/player/93codemonkey/games/2023/09", "ht

In [169]:
csv_data = []
api_cache = {}

csv_data << ["d_time","t_type","my_color","opponent","my_elo","opponent_elo","opponent_curr_elo",
  "my_curr_elo","result","result_type","url","pgn", "moves_3", "moves_4", "moves_5", "moves_6", "moves_9"]

games_array.each_with_index do |game, idx|
  
  t_type = game["time_class"]
  t_type += "_" + game["rules"] if game["rules"] != "chess"
  url = game["url"]
  params = extract_pgn_params(game["pgn"])

  d_time = extract_time(params)
  
  white = params[:White]
  white_elo = params[:WhiteElo]
  black = params[:Black]
  black_elo = params[:BlackElo]
  
  my_color, opponent_color = white == username ? ["WHITE", "BLACK"] : ["BLACK", "WHITE"]
  my_elo, opponent_elo = white == username ? [white_elo, black_elo] : [black_elo, white_elo]

  opponent = game[opponent_color.downcase]["username"]
  
  result_str = params[:Termination]
  result_type = result_str.split.last
  result =
    if result_str.include?("drawn")
      "DRAW"
    elsif result_str.split[0] == username
      "WIN"
    else
      "LOSE"
    end
  
  my_curr_elo = call_stats(username.downcase, api_cache, t_type)
  opponent_curr_elo = call_stats(opponent.downcase, api_cache, t_type)
  pgn = params[:pgn]
  moves_3 = extract_moves(pgn)[0..4].join(' ')
  moves_4 = extract_moves(pgn)[0..6].join(' ')
  moves_5 = extract_moves(pgn)[0..8].join(' ')
  moves_6 = extract_moves(pgn)[0..10].join(' ')
  moves_9 = extract_moves(pgn)[0..15].join(' ')

  csv_data << [d_time,t_type,my_color,opponent,my_elo,opponent_elo,opponent_curr_elo,my_curr_elo,result,result_type,url,
    pgn, moves_3, moves_4, moves_5, moves_6, moves_9]
  
end

puts "Successfully Parsed"

https://api.chess.com/pub/player/93codemonkey/stats
https://api.chess.com/pub/player/waytoofried/stats
https://api.chess.com/pub/player/marton2008/stats
https://api.chess.com/pub/player/williamg08/stats
https://api.chess.com/pub/player/mazzolo/stats
https://api.chess.com/pub/player/akiserg/stats
https://api.chess.com/pub/player/jjknopf/stats
https://api.chess.com/pub/player/amir_rze/stats
https://api.chess.com/pub/player/cafer_huseinov/stats
https://api.chess.com/pub/player/mastrian/stats
https://api.chess.com/pub/player/awesam85/stats
https://api.chess.com/pub/player/banans67/stats
https://api.chess.com/pub/player/thlaorans/stats
https://api.chess.com/pub/player/moayana/stats
https://api.chess.com/pub/player/newplato/stats
https://api.chess.com/pub/player/m_amphetamine/stats
https://api.chess.com/pub/player/fox1708/stats
https://api.chess.com/pub/player/arstapan/stats
https://api.chess.com/pub/player/nogood666/stats
https://api.chess.com/pub/player/maxim7802/stats
https://api.chess.co

https://api.chess.com/pub/player/sjaesq/stats
https://api.chess.com/pub/player/sirhumphreygilbert/stats
https://api.chess.com/pub/player/lukas1984w/stats
https://api.chess.com/pub/player/kaledempire/stats
https://api.chess.com/pub/player/daselzavon/stats
https://api.chess.com/pub/player/wikulec/stats
https://api.chess.com/pub/player/psam0/stats
https://api.chess.com/pub/player/folk1983/stats
https://api.chess.com/pub/player/santiago9196/stats
https://api.chess.com/pub/player/epicnine/stats
https://api.chess.com/pub/player/ismaelmanurung2018/stats
https://api.chess.com/pub/player/zusammenauf/stats
https://api.chess.com/pub/player/kiwixabbu/stats
https://api.chess.com/pub/player/pawnup31602/stats
https://api.chess.com/pub/player/tonybn7/stats
https://api.chess.com/pub/player/bizon444/stats
https://api.chess.com/pub/player/szary669/stats
https://api.chess.com/pub/player/vsegure/stats
https://api.chess.com/pub/player/frov/stats
https://api.chess.com/pub/player/flaco62/stats
https://api.che

https://api.chess.com/pub/player/yoyoyoyo81/stats
https://api.chess.com/pub/player/rybickij/stats
https://api.chess.com/pub/player/simo153a/stats
https://api.chess.com/pub/player/23409m/stats
https://api.chess.com/pub/player/selvaris/stats
https://api.chess.com/pub/player/kajlonn/stats
https://api.chess.com/pub/player/mikounet/stats
https://api.chess.com/pub/player/d_mickens/stats
https://api.chess.com/pub/player/aaposadao/stats
https://api.chess.com/pub/player/metaru_sama/stats
https://api.chess.com/pub/player/physiologicalsigh/stats
https://api.chess.com/pub/player/nixam25/stats
https://api.chess.com/pub/player/hosseinrazaghian54/stats
https://api.chess.com/pub/player/tomnap/stats
https://api.chess.com/pub/player/evgeniyrussia81/stats
https://api.chess.com/pub/player/rb270/stats
https://api.chess.com/pub/player/biggie_ren/stats
https://api.chess.com/pub/player/korujao/stats
https://api.chess.com/pub/player/edewaldo/stats
https://api.chess.com/pub/player/rudysutawijaya41/stats
https:/

https://api.chess.com/pub/player/mariammel/stats
https://api.chess.com/pub/player/goldenstatewarriorswin/stats
https://api.chess.com/pub/player/marseillais_13/stats
https://api.chess.com/pub/player/ruszczyk/stats
https://api.chess.com/pub/player/ed_josh_2011/stats
https://api.chess.com/pub/player/lbkaiser/stats
https://api.chess.com/pub/player/andrus1965/stats
https://api.chess.com/pub/player/bruceleejkdchess/stats
https://api.chess.com/pub/player/jamesjdart/stats
https://api.chess.com/pub/player/silak75b/stats
https://api.chess.com/pub/player/oldinter63/stats
https://api.chess.com/pub/player/saswathacademy/stats
https://api.chess.com/pub/player/sadebe/stats
https://api.chess.com/pub/player/bigvaluedaddy/stats
https://api.chess.com/pub/player/rakunfaru/stats
https://api.chess.com/pub/player/brye80/stats
https://api.chess.com/pub/player/naxara05/stats
https://api.chess.com/pub/player/fourohfour/stats
https://api.chess.com/pub/player/grattatout/stats
https://api.chess.com/pub/player/szon

https://api.chess.com/pub/player/broletarian/stats
https://api.chess.com/pub/player/hemaseva/stats
https://api.chess.com/pub/player/zorglubbb/stats
https://api.chess.com/pub/player/maciul/stats
https://api.chess.com/pub/player/drt025/stats
https://api.chess.com/pub/player/ercefal/stats
https://api.chess.com/pub/player/bluefire69/stats
https://api.chess.com/pub/player/jacenty01/stats
https://api.chess.com/pub/player/da-d0/stats
https://api.chess.com/pub/player/elfrainthelight/stats
https://api.chess.com/pub/player/ererer1234554/stats
https://api.chess.com/pub/player/tamerkartal/stats
https://api.chess.com/pub/player/cannedgood/stats
https://api.chess.com/pub/player/wilfred748/stats
https://api.chess.com/pub/player/sunshinedaydreamer/stats
https://api.chess.com/pub/player/applejuicedad/stats
https://api.chess.com/pub/player/dolwen/stats
https://api.chess.com/pub/player/poorcollegeboy/stats
https://api.chess.com/pub/player/alekseiromanov/stats
https://api.chess.com/pub/player/bmcgavig/sta

...

https://api.chess.com/pub/player/christiancasa/stats
https://api.chess.com/pub/player/benrace64/stats
https://api.chess.com/pub/player/algocreativo/stats
https://api.chess.com/pub/player/greglan/stats
https://api.chess.com/pub/player/vallyvally/stats
https://api.chess.com/pub/player/epicnewbie212121212/stats
https://api.chess.com/pub/player/theshootix/stats
https://api.chess.com/pub/player/troy1331/stats
https://api.chess.com/pub/player/leegio30/stats
https://api.chess.com/pub/player/joberdo/stats
https://api.chess.com/pub/player/sethber/stats
https://api.chess.com/pub/player/luca0505/stats
https://api.chess.com/pub/player/uncletom92/stats
https://api.chess.com/pub/player/remaythebear/stats
https://api.chess.com/pub/player/zlyniedobry/stats
https://api.chess.com/pub/player/superlazza/stats
https://api.chess.com/pub/player/gokugogo/stats
https://api.chess.com/pub/player/jaitravelworld/stats
https://api.chess.com/pub/player/antogocaj/stats
https://api.chess.com/pub/player/rileyoneal/stat

https://api.chess.com/pub/player/skeptic50/stats
https://api.chess.com/pub/player/evgeniq92/stats
https://api.chess.com/pub/player/vaux76/stats
https://api.chess.com/pub/player/dragonclawss/stats
https://api.chess.com/pub/player/sohrab1978/stats
https://api.chess.com/pub/player/sumerm/stats
https://api.chess.com/pub/player/tashapluto/stats
https://api.chess.com/pub/player/hassmo_o/stats
https://api.chess.com/pub/player/namranpan/stats
https://api.chess.com/pub/player/pohsibpair/stats
https://api.chess.com/pub/player/lordbattenberg/stats
https://api.chess.com/pub/player/allan_alves/stats
https://api.chess.com/pub/player/slowracer/stats
https://api.chess.com/pub/player/chessdaddyvp/stats
https://api.chess.com/pub/player/charlesvanasse/stats
https://api.chess.com/pub/player/azer0s/stats
https://api.chess.com/pub/player/schlecky/stats
https://api.chess.com/pub/player/euler90/stats
https://api.chess.com/pub/player/kepler33/stats
https://api.chess.com/pub/player/x-6719517043/stats
https://ap

https://api.chess.com/pub/player/yashpatil_810/stats
https://api.chess.com/pub/player/poofy1983/stats
https://api.chess.com/pub/player/badblistah/stats
https://api.chess.com/pub/player/warl0r/stats
https://api.chess.com/pub/player/monkey_4me/stats
https://api.chess.com/pub/player/alvamico/stats
https://api.chess.com/pub/player/zigzagg45/stats
https://api.chess.com/pub/player/estevaoxadrez/stats
https://api.chess.com/pub/player/axnt33/stats
https://api.chess.com/pub/player/vaibhavmisra9231/stats
https://api.chess.com/pub/player/kars4444/stats
https://api.chess.com/pub/player/vee_r_six/stats
https://api.chess.com/pub/player/elnacho32tri/stats
https://api.chess.com/pub/player/kalimoxto/stats
https://api.chess.com/pub/player/nthtimelucky/stats
https://api.chess.com/pub/player/karel1512/stats
https://api.chess.com/pub/player/berco555/stats
https://api.chess.com/pub/player/hschork/stats
https://api.chess.com/pub/player/zevulous/stats
https://api.chess.com/pub/player/legit_chess411/stats
http

https://api.chess.com/pub/player/jakepc1/stats
https://api.chess.com/pub/player/sinber1/stats
https://api.chess.com/pub/player/birkichess/stats
https://api.chess.com/pub/player/markoni27/stats
https://api.chess.com/pub/player/yannis94/stats
https://api.chess.com/pub/player/sumsong/stats
https://api.chess.com/pub/player/tghw/stats
https://api.chess.com/pub/player/paulmorud/stats
https://api.chess.com/pub/player/aldradur/stats
https://api.chess.com/pub/player/hiskiasz/stats
https://api.chess.com/pub/player/dimaschneid/stats
https://api.chess.com/pub/player/41yunus72/stats
https://api.chess.com/pub/player/stics007/stats
https://api.chess.com/pub/player/sverretl/stats
https://api.chess.com/pub/player/orgsalsa/stats
https://api.chess.com/pub/player/ypeeri/stats
https://api.chess.com/pub/player/ireade/stats
https://api.chess.com/pub/player/veg1987/stats
https://api.chess.com/pub/player/the_naed/stats
https://api.chess.com/pub/player/roarhove/stats
https://api.chess.com/pub/player/siegel78/st

https://api.chess.com/pub/player/oncemoreman/stats
https://api.chess.com/pub/player/hugocarboni/stats
https://api.chess.com/pub/player/mangiaspaghetti_007/stats
https://api.chess.com/pub/player/aditya_kresna/stats
https://api.chess.com/pub/player/skmen/stats
https://api.chess.com/pub/player/j_godoy/stats
https://api.chess.com/pub/player/alikovichyura/stats
https://api.chess.com/pub/player/ranses1968/stats
https://api.chess.com/pub/player/agoober579/stats
https://api.chess.com/pub/player/rabens/stats
https://api.chess.com/pub/player/thequietstep/stats
https://api.chess.com/pub/player/stevenrale/stats
https://api.chess.com/pub/player/plouks01/stats
https://api.chess.com/pub/player/dummy_11/stats
https://api.chess.com/pub/player/peblo11/stats
https://api.chess.com/pub/player/paulo_bass/stats
https://api.chess.com/pub/player/oprodospro/stats
https://api.chess.com/pub/player/kosty1978/stats
https://api.chess.com/pub/player/haydenpotts/stats
https://api.chess.com/pub/player/sheikinbouti/stat

In [171]:
CSV.open(csv_file, 'w', write_headers: true, headers: []) do |csv|
  csv_data.each do |row|
    csv << row
  end
end

[["d_time", "t_type", "my_color", "opponent", "my_elo", "opponent_elo", "opponent_curr_elo", "my_curr_elo", "result", "result_type", "url", "pgn", "moves_3", "moves_4", "moves_5", "moves_6", "moves_9"], [2023-01-01 07:58:34 +0530, "blitz", "BLACK", "WayTooFried", "1271", "1212", 1046, 1480, "LOSE", "checkmate", "https://www.chess.com/game/live/66298861847", "1. e4 {[%clk 0:03:02]} 1... d6 {[%clk 0:02:58.9]} 2. d4 {[%clk 0:03:02.9]} 2... Nf6 {[%clk 0:03:00]} 3. Nc3 {[%clk 0:03:03.1]} 3... g6 {[%clk 0:02:57.1]} 4. Be3 {[%clk 0:03:03.9]} 4... Bg7 {[%clk 0:02:45.8]} 5. f3 {[%clk 0:03:02.4]} 5... c6 {[%clk 0:02:47.4]} 6. Qd2 {[%clk 0:03:03.7]} 6... Qb6 {[%clk 0:02:49]} 7. d5 {[%clk 0:03:00.5]} 7... Qxb2 {[%clk 0:02:49.1]} 8. Rb1 {[%clk 0:02:47.4]} 8... Qa3 {[%clk 0:02:49.4]} 9. Nh3 {[%clk 0:02:28.8]} 9... Bxh3 {[%clk 0:02:44]} 10. gxh3 {[%clk 0:02:28.2]} 10... Na6 {[%clk 0:02:44.1]} 11. Rxb7 {[%clk 0:02:23.7]} 11... Nb4 {[%clk 0:02:43.4]} 12. Nb5 {[%clk 0:02:10.5]} 12... Nxc2+ {[%clk 0:02:3

## Chess Analytics

In [172]:
# Overall Results

daru_df = Daru::DataFrame.from_csv(read_file)
grouped_data = daru_df['t_type','d_time','result','my_elo','opponent_elo'].group_by(['t_type'])
result = []

grouped_data.each_group do |games|
  category = games['t_type'].at(0)
  cnt = games.size
  win = games.where(games['result'].eq("WIN")).size
  loss = games.where(games['result'].eq("LOSE")).size
  net_wins = (win-loss).to_s
  net_wins = "+" + (win-loss).to_s if (win-loss) > 0
  draw = games.where(games['result'].eq("DRAW")).size
  oldest_rating = games.sort(['d_time']).row_at(0)['my_elo']
  
  result << [category, cnt, win, loss, draw, oldest_rating, net_wins]
  
end

Daru::DataFrame.rows(result, order: ['Category', 'Number of Games', 'Wins', 'Loss', 'Draw', 'Start Elo', 'Net Wins'])
.sort(['Number of Games'],ascending: [false])

#<Daru::DataFrame(5x7)>
                        Category Number of Games            Wins            Loss            Draw       Start Elo        Net Wins
               2          bullet            1638             813             796              29            1275             +17
               0           blitz            1389             691             660              38            1271             +31
               4           rapid             409             198             192              19            1711              +6
               3           daily               5               5               0               0            1380              +5
               1  blitz_chess960               2               1               1               0            1293               0

In [212]:
# Rematch Opponents

grouped_data = daru_df.group_by(['t_type', 'opponent'])
result = []
min_games = 5

grouped_data.each_group do |games|
  category = games['t_type'].at(0)
  next if ["bullet","blitz","rapid","daily"].none?(category)
  opponent = games['opponent'].at(0)
  cnt = games.size
  
  next if cnt < min_games
  white_games = games.where(games['my_color'].eq("WHITE")).size
  white_wins = games.where(games['result'].eq("WIN") & games['my_color'].eq("WHITE")).size
  white_result = white_wins.to_s + "/" + white_games.to_s
  black_games = games.where(games['my_color'].eq("BLACK")).size
  black_wins = games.where(games['result'].eq("WIN") & games['my_color'].eq("BLACK")).size
  black_result = black_wins.to_s + "/" + black_games.to_s
  win = white_wins + black_wins
  loss = games.where(games['result'].eq("LOSE")).size
  net_result = "+" + win.to_s + " -" + loss.to_s + " =" + (cnt-win-loss).to_s
  
  opp_elo = games.sort(['d_time']).row_at(0)['opponent_elo']
  opp_elo_now = games['opponent_curr_elo'].at(0)
  my_curr_elo = games['my_curr_elo'].at(0)
  opp_growth = opp_elo_now - opp_elo
  opp_growth = "+" + opp_growth.to_s if opp_growth > 0
  
  result << [category, opponent, cnt, win, white_result, black_result, net_result, opp_elo, opp_elo_now, my_curr_elo, opp_growth]
  
end

Daru::DataFrame.rows(result, order: ['Category', 'Opponent', 'Games', 'Wins', 'White wins', 'Black wins', 'Net Result', 'Opp Then','Opp Now', 'Me Now', 'Opp Growth'])
.sort(['Games', 'Opp Now'], ascending: [false,false])

#<Daru::DataFrame(10x11)>
              Category   Opponent      Games       Wins White wins Black wins Net Result   Opp Then    Opp Now     Me Now Opp Growth
          2     bullet Pranavnar0         18          9        6/9        3/9   +9 -9 =0       1273       1354       1312        +81
          1     bullet   LuckyJAL          8          4        2/4        2/4   +4 -4 =0       1279       1390       1312       +111
          5     bullet archit1234          8          5        2/4        3/4   +5 -3 =0       1335       1253       1312        -82
          4     bullet TamerKarta          7          2        2/3        0/4   +2 -3 =2       1241       1343       1312       +102
          3     bullet Sonoftheki          7          1        1/4        0/3   +1 -6 =0       1313       1248       1312        -65
          9      rapid   xan51311          6          1        0/3        1/3   +1 -4 =1       1786       1782       1741         -4
          8      rapid    Tricko3          6          1        1/3        0/3   +1 -5 =0       1600       1415       1741       -185
          0     bullet    4fitplz          6          2        2/3        0/3   +2 -4 =0       1257       1375       1312       +118
          7     bullet  xRoland22          5          1        0/3        1/2   +1 -4 =0       1419       1317       1312       -102
          6     bullet liebrelent          5          1        0/2        1/3   +1 -3 =1       1202        771       1312       -431

In [215]:
# Interesting Wins
c_games = daru_df
.group_by(['t_type'])

result = []

c_games.each_group do |games|
  category = games['t_type'].at(0)
  next if ["blitz","rapid"].none?(category)
  top_games = games.where(games['result'].eq("WIN")).sort(['opponent_curr_elo'], ascending: false).head(3)
  
  top_games.each_row do |game|
    opp = game['opponent']
    my_color = game['my_color']
    opp_elo = game['opponent_elo']
    opp_now = game['opponent_curr_elo']
    result_type = game['result_type']
    game_link = game['url']
    
    result << [category, opp, my_color,opp_elo, opp_now, result_type, game_link]
  end
end

Daru::DataFrame.rows(result, order: ['Category', 'Opponent', 'My Color', 'Opp Then' ,'Opp Now', 'Result' ,'Game'])
.sort(['Category'], ascending: false)

#<Daru::DataFrame(6x7)>
              Category   Opponent   My Color   Opp Then    Opp Now     Result       Game
          3      rapid iqraathema      BLACK       1758       2111  checkmate https://ww
          4      rapid Kingabhina      WHITE       1590       2049 resignatio https://ww
          5      rapid Stalinguar      WHITE       1676       2035  checkmate https://ww
          0      blitz     kvvkxo      WHITE       1295       2047  checkmate https://ww
          1      blitz    tonybn7      WHITE       1437       1924       time https://ww
          2      blitz    Iudexxx      WHITE       1431       1901 resignatio https://ww

In [219]:
# Interesting Losses

c_games = daru_df
.group_by(['t_type'])

result = []

c_games.each_group do |games|
  category = games['t_type'].at(0)
  next if ["blitz","rapid"].none?(category)
  top_games = games.where(games['result'].eq("LOSE")).sort(['opponent_curr_elo'], ascending: true).head(3)
  
  top_games.each_row do |game|
    opp = game['opponent']
    my_color = game['my_color']
    opp_elo = game['opponent_elo']
    opp_now = game['opponent_curr_elo']
    result_type = game['result_type']
    game_link = game['url']
    
    result << [category, opp, my_color,opp_elo, opp_now, game_link]
  end
end

Daru::DataFrame.rows(result, order: ['Category', 'Opponent', 'My Color', 'Opp Then' ,'Opp Now', 'Game'])
.sort(['Category'], ascending: false)

#<Daru::DataFrame(6x6)>
              Category   Opponent   My Color   Opp Then    Opp Now       Game
          3      rapid daviduzbek      BLACK       1452       1268 https://ww
          4      rapid Cesare1976      BLACK       1555       1270 https://ww
          5      rapid Rustam_Che      WHITE       1482       1311 https://ww
          0      blitz       Hwem      WHITE       1496        462 https://ww
          1      blitz    lts_Mee      BLACK       1495        981 https://ww
          2      blitz WayTooFrie      BLACK       1212       1046 https://ww

In [176]:
# Games in each side
w_games = daru_df.where(daru_df['my_color'].eq('WHITE'))['moves_3','moves_4','moves_5','moves_6','moves_9','result']
b_games = daru_df.where(daru_df['my_color'].eq('BLACK'))['moves_3','moves_4','moves_5','moves_6','moves_9','result']
daru_df['my_color','pgn'].group_by('my_color').count()

#<Daru::DataFrame(2x1)>
         pgn
 BLACK  1716
 WHITE  1727

## Move Orders

In [177]:
count_map = Hash.new{ |h, k| h[k] = Hash.new(0) }

w_games.each_row do |row|
  count_map[row['moves_3']][row['result']] += 1
end

result_df = Daru::DataFrame.rows(count_map.map { |moves, counts| [moves, counts['WIN'], counts['LOSE'], counts['DRAW']] },
                                  order: [:moves_3, :WIN, :LOSE, :DRAW],
                                  index: false)

result_df.add_vector(:total, result_df[:WIN] + result_df[:LOSE] + result_df[:DRAW])

result_df.sort([:total], ascending: false)[:moves_3,:total, :WIN,:LOSE, :DRAW ].head(5)

#<Daru::DataFrame(5x5)>
               moves_3      total        WIN       LOSE       DRAW
          0 e4 e5 Nf3         368        190        169          9
          8 e4 c6 Nf3         254        132        118          4
          3 e4 c5 Nf3         115         64         49          2
          6 e4 e6 Nf3          98         54         42          2
          2 e4 c5 Nf3          95         46         45          4

In [217]:
count_map = Hash.new{ |h, k| h[k] = Hash.new(0) }

b_games.each_row do |row|
  count_map[row['moves_3']][row['result']] += 1
end

result_df = Daru::DataFrame.rows(count_map.map { |moves, counts| [moves, counts['WIN'], counts['LOSE'], counts['DRAW']] },
                                  order: [:moves_3, :WIN, :LOSE, :DRAW],
                                  index: false)

result_df.add_vector(:total, result_df[:WIN] + result_df[:LOSE] + result_df[:DRAW])

result_df.sort([:total], ascending: false)[:moves_3,:total, :WIN,:LOSE, :DRAW ].head(5)

#<Daru::DataFrame(5x5)>
               moves_3      total        WIN       LOSE       DRAW
          0 e4 d6 d4 N        336        177        144         15
          6 e4 d6 Nf3         186         98         85          3
         12 e4 d6 d4 N         97         48         43          6
         19 d4 Nf6 c4          68         24         42          2
         13 d4 d6 c4 N         63         35         27          1

In [178]:
count_map = Hash.new{ |h, k| h[k] = Hash.new(0) }

w_games.each_row do |row|
  count_map[row['moves_4']][row['result']] += 1
end

result_df = Daru::DataFrame.rows(count_map.map { |moves, counts| [moves, counts['WIN'], counts['LOSE'], counts['DRAW']] },
                                  order: [:moves_4, :WIN, :LOSE, :DRAW],
                                  index: false)

result_df.add_vector(:total, result_df[:WIN] + result_df[:LOSE] + result_df[:DRAW])

result_df.sort([:total], ascending: false)[:moves_4,:total, :WIN,:LOSE, :DRAW ].head(5)

#<Daru::DataFrame(5x5)>
               moves_4      total        WIN       LOSE       DRAW
         20 e4 c6 Nf3         157         83         73          1
         19 e4 e5 Nf3         128         66         57          5
          0 e4 e5 Nf3          59         30         27          2
         30 e4 c6 Nf3          43         21         21          1
         17 e4 c5 Nf3          42         27         15          0

In [179]:
count_map = Hash.new{ |h, k| h[k] = Hash.new(0) }

w_games.each_row do |row|
  count_map[row['moves_5']][row['result']] += 1
end

result_df = Daru::DataFrame.rows(count_map.map { |moves, counts| [moves, counts['WIN'], counts['LOSE'], counts['DRAW']] },
                                  order: [:moves_5, :WIN, :LOSE, :DRAW],
                                  index: false)

result_df.add_vector(:total, result_df[:WIN] + result_df[:LOSE] + result_df[:DRAW])

result_df.sort([:total], ascending: false)[:moves_5,:total, :WIN,:LOSE, :DRAW].head(5)

#<Daru::DataFrame(5x5)>
               moves_5      total        WIN       LOSE       DRAW
        303 e4 e5 Nf3          52         26         24          2
        249 e4 c6 Nf3          51         28         23          0
        120 e4 e5 Nf3          39         17         19          3
         17 e4 c5 Nf3          32         23          9          0
         69 e4 e5 Nf3          28         15         13          0

In [180]:
count_map = Hash.new{ |h, k| h[k] = Hash.new(0) }

w_games.each_row do |row|
  count_map[row['moves_6']][row['result']] += 1
end

result_df = Daru::DataFrame.rows(count_map.map { |moves, counts| [moves, counts['WIN'], counts['LOSE'], counts['DRAW']] },
                                  order: [:moves_6, :WIN, :LOSE, :DRAW],
                                  index: false)

result_df.add_vector(:total, result_df[:WIN] + result_df[:LOSE] + result_df[:DRAW])

result_df.sort([:total], ascending: false)[:moves_6,:total, :WIN,:LOSE, :DRAW ].head(5)

#<Daru::DataFrame(5x5)>
               moves_6      total        WIN       LOSE       DRAW
        366 e4 e5 Nf3          50         26         22          2
        304 e4 c6 Nf3          43         24         19          0
        142 e4 e5 Nf3          38         16         19          3
         77 e4 e5 Nf3          26         14         12          0
        367 e4 e5 Nf3          23         11         12          0

In [181]:
count_map = Hash.new{ |h, k| h[k] = Hash.new(0) }

w_games.each_row do |row|
  count_map[row['moves_9']][row['result']] += 1
end

result_df = Daru::DataFrame.rows(count_map.map { |moves, counts| [moves, counts['WIN'], counts['LOSE'], counts['DRAW']] },
                                  order: [:moves_9, :WIN, :LOSE, :DRAW],
                                  index: false)

result_df.add_vector(:total, result_df[:WIN] + result_df[:LOSE] + result_df[:DRAW])

result_df.sort([:total], ascending: false)[:moves_9,:total,:WIN,:LOSE, :DRAW ].head(5)

#<Daru::DataFrame(5x5)>
               moves_9      total        WIN       LOSE       DRAW
        409 e4 e5 Nf3          15          9          4          2
        479 e4 e5 Nf3          11          4          7          0
        421 e4 c6 Nf3           9          4          5          0
         91 e4 e5 Nf3           6          4          2          0
        211 e4 e5 Nf3           3          2          1          0

## Openings

In [202]:
#Caro Variations as White
move_order = 'e4 c6 Nf3 d5 Nc3'

caro, caro_wins, caro_draws, caro_losses, caro_net = opening_results(move_order, w_games, 5)
caro.group_by(['variation', 'result']).count

#<Daru::DataFrame(16x1)>
                          moves_9
 e4 c6 Nf3        DRAW          2
                  LOSE         25
                   WIN         23
 e4 c6 Nf3        LOSE          6
                   WIN          3
 e4 c6 Nf3        LOSE          1
 e4 c6 Nf3        DRAW          1
                  LOSE         10
                   WIN         17
 e4 c6 Nf3        DRAW          1
                  LOSE         74
                   WIN         83
 e4 c6 Nf3        LOSE          1
                   WIN          3
 e4 c6 Nf3        LOSE          1
 e4 c6 Nf3         WIN          1

In [203]:
#Stafford Variations as White
move_order = 'e4 e5 Nf3 Nf6 Nxe5 Nc6 Nxc6 dxc6 d3 Bc5 Be2'

stafford, stafford_wins, stafford_draws, stafford_losses, stafford_net = opening_results(move_order, w_games, 11)
stafford.group_by(['variation', 'result']).count

#<Daru::DataFrame(9x1)>
                          moves_9
 e4 e5 Nf3         WIN          1
 e4 e5 Nf3         WIN          1
 e4 e5 Nf3        LOSE          1
                   WIN          1
 e4 e5 Nf3        LOSE          1
 e4 e5 Nf3         WIN          2
 e4 e5 Nf3         WIN          1
 e4 e5 Nf3        LOSE         10
                   WIN          8

In [204]:
#Scandinavian Variations as White
move_order = 'e4 d5 exd5 Qxd5 Nf3'

scandi, scandi_wins, scandi_draws, scandi_losses, scandi_net = opening_results(move_order, w_games, 5)
scandi.group_by(['variation', 'result']).count

#<Daru::DataFrame(12x1)>
                          moves_9
 e4 d5 exd5        WIN          2
 e4 d5 exd5       LOSE          8
                   WIN          4
 e4 d5 exd5        WIN          1
 e4 d5 exd5       LOSE          1
                   WIN          4
 e4 d5 exd5        WIN          1
 e4 d5 exd5        WIN          1
 e4 d5 exd5       LOSE          1
                   WIN          4
 e4 d5 exd5        WIN          1
 e4 d5 exd5       DRAW          1

In [205]:
#Sicilian Variations as White
move_order = 'e4 c5 Nf3'

sicili, sicili_wins, sicili_draws, sicili_losses, sicili_net = opening_results(move_order, w_games, 3)
sicili.group_by(['variation', 'result']).count

#<Daru::DataFrame(18x1)>
                          moves_9
 e4 c5 Nf3        DRAW          3
                  LOSE         73
                   WIN         83
 e4 c5 Nf3        LOSE          2
                   WIN          2
 e4 c5 Nf3        LOSE          3
                   WIN          2
 e4 c5 Nf3        LOSE          1
 e4 c5 Nf3        LOSE          1
                   WIN          1
 e4 c5 Nf3        DRAW          4
                  LOSE         59
                   WIN         61
 e4 c5 Nf3        DRAW          1
                  LOSE         33
                   WIN         29
 e4 c5 Nf3        LOSE         10
                   WIN          6

In [206]:
#Italian Variations as White
move_order = 'e4 e5 Nf3 Nc6 Bc4'

ita, ita_wins, ita_draws, ita_losses, ita_net = opening_results(move_order, w_games, 5)
ita.group_by(['variation', 'result']).count

#<Daru::DataFrame(24x1)>
                          moves_9
 e4 e5 Nf3         WIN          2
 e4 e5 Nf3        DRAW          5
                  LOSE         63
                   WIN         73
 e4 e5 Nf3         WIN          2
 e4 e5 Nf3        LOSE          8
                   WIN          3
 e4 e5 Nf3         WIN          1
 e4 e5 Nf3        LOSE          5
                   WIN          6
 e4 e5 Nf3        DRAW          2
                  LOSE         50
                   WIN         57
 e4 e5 Nf3         WIN          1
 e4 e5 Nf3         WIN          1
 e4 e5 Nf3        DRAW          1
                  LOSE         15
                   WIN         15
 e4 e5 Nf3        LOSE         12
                   WIN          8
 e4 e5 Nf3        LOSE          1
 e4 e5 Nf3        DRAW          1
                  LOSE         15
                   WIN         19

In [207]:
#Pirc Variations as Black
move_order = 'e4 d6 d4 Nf6'

pirc, pirc_wins, pirc_draws, pirc_losses, pirc_net = opening_results(move_order, b_games, 4)
pirc.group_by(['variation', 'result']).count

#<Daru::DataFrame(29x1)>
                          moves_9
 e4 d6 d4 N       LOSE          3
 e4 d6 d4 N       DRAW          6
                  LOSE         42
                   WIN         48
 e4 d6 d4 N        WIN          1
 e4 d6 d4 N       DRAW          1
                  LOSE          1
 e4 d6 d4 N       LOSE          2
                   WIN          1
 e4 d6 d4 N       DRAW         15
                  LOSE        144
                   WIN        176
 e4 d6 d4 N       LOSE         11
                   WIN          6
 e4 d6 d4 N       LOSE          1
 e4 d6 d4 N       DRAW          1
                  LOSE          1
                   WIN          4
 e4 d6 d4 N       LOSE          1
 e4 d6 d4 N       LOSE          1
                   WIN          2
 e4 d6 d4 N        WIN          3
 e4 d6 d4 N       DRAW          1
 e4 d6 d4 N       LOSE          7
                   WIN         16
 e4 d6 d4 N       LOSE         10
                   WIN          4
 e4 d6 d4 N        WIN          3
 e4 d6 d4 N       LOSE          1

In [208]:
#Indian Game as Black
move_order = 'd4 Nf6 Bf4 e6' 

indian, indian_wins, indian_draws, indian_losses, indian_net = opening_results(move_order, b_games, 4)
indian.group_by(['variation', 'result']).count

#<Daru::DataFrame(9x1)>
                          moves_9
 d4 Nf6 Bf4       LOSE          3
                   WIN          1
 d4 Nf6 Bf4       LOSE          9
                   WIN         10
 d4 Nf6 Bf4        WIN          1
 d4 Nf6 Bf4       DRAW          1
                  LOSE          9
                   WIN         15
 d4 Nf6 Bf4        WIN          2

In [218]:
#Nimzo Indian Variations as Black
move_order = 'd4 Nf6 c4 e6'

nimzo, nimzo_wins, nimzo_draws, nimzo_losses, nimzo_net = opening_results(move_order, b_games, 4)
nimzo.group_by(['variation', 'result']).count

#<Daru::DataFrame(15x1)>
                          moves_9
 d4 Nf6 c4         WIN          1
 d4 Nf6 c4        DRAW          2
                  LOSE         42
                   WIN         24
 d4 Nf6 c4        LOSE         10
                   WIN          3
 d4 Nf6 c4        LOSE          2
                   WIN          2
 d4 Nf6 c4        LOSE          1
 d4 Nf6 c4        LOSE          1
                   WIN          1
 d4 Nf6 c4         WIN          1
 d4 Nf6 c4         WIN          1
 d4 Nf6 c4        LOSE          1
                   WIN          1

In [210]:
print "Caro : ","+",caro_wins,"-",caro_losses,"=",caro_draws," [#{caro_net}]\n"
print "Stafford : ","+",stafford_wins,"-",stafford_losses,"=",stafford_draws," [#{stafford_net}]\n"
print "Scandinavian : ","+",scandi_wins,"-",scandi_losses,"=",scandi_draws," [#{scandi_net}]\n"
print "Sicilian : ","+",sicili_wins,"-",sicili_losses,"=",sicili_draws," [#{sicili_net}]\n"
print "Italian : ","+",ita_wins,"-",ita_losses,"=",ita_draws," [#{ita_net}]\n"
print "Pirc : ","+",pirc_wins,"-",pirc_losses,"=",pirc_draws," [#{pirc_net}]\n"
print "Indian Game : ","+",indian_wins,"-",indian_losses,"=",indian_draws," [#{indian_net}]\n"
print "Nimzo-Indian Game : ","+",nimzo_wins,"-",nimzo_losses,"=",nimzo_draws," [#{nimzo_net}]\n"

Caro : +130-118=4 [12]
Stafford : +14-12=0 [2]
Scandinavian : +18-10=1 [8]
Sicilian : +184-182=8 [2]
Italian : +188-169=9 [19]
Pirc : +264-225=24 [39]
Indian Game : +29-21=1 [8]
Nimzo-Indian Game : +34-57=2 [-23]
